In [26]:
import numpy as np
import helper_functions as hf
from scipy.stats import kurtosis, skew
from biosppy.signals.eeg import eeg
from neurokit import emg_process
from sklearn.model_selection import StratifiedKFold, cross_val_score
from keras.models import Sequential
from keras.wrappers.scikit_learn import KerasClassifier
from keras.layers import Dense, Activation, Flatten, Dropout, BatchNormalization, LeakyReLU, \
    Conv1D, MaxPooling1D, GlobalAveragePooling1D, TimeDistributed, LSTM


In [27]:
X_train_eeg1, _ = hf.read_csv_to_matrix("task5/input/train_eeg1.csv", "Id")
X_train_eeg2, _ = hf.read_csv_to_matrix("task5/input/train_eeg2.csv", "Id")
X_train_emg, _ = hf.read_csv_to_matrix("task5/input/train_emg.csv", "Id")
X_test_eeg1, _ = hf.read_csv_to_matrix("task5/input/test_eeg1.csv", "Id")
X_test_eeg2, _ = hf.read_csv_to_matrix("task5/input/test_eeg2.csv", "Id")
X_test_emg, _ = hf.read_csv_to_matrix("task5/input/test_emg.csv", "Id")
y_train, _ = hf.read_csv_to_matrix("task5/input/train_labels.csv", "Id")
_, test_index = hf.read_csv_to_matrix("task5/input/sample.csv", "Id")
y_train = np.squeeze(y_train)


In [198]:
from keras.metrics import categorical_accuracy, mae

def cnn_model():
    filt = 4
    
    model = Sequential()

    model.add(Conv1D(name="conv1", filters=2**filt, kernel_size=3, input_shape=(200, 1)))
    model.add(LeakyReLU(name="act1", alpha=.01))
    model.add(MaxPooling1D(name="mp1", pool_size=2))
    
    model.add(Conv1D(name="conv2", filters=2**(filt+1), kernel_size=3))
    model.add(LeakyReLU(name="act2", alpha=.01))
    model.add(MaxPooling1D(name="mp2", pool_size=2))

    model.add(Conv1D(name="conv3", filters=2**(filt+2), kernel_size=3))
    model.add(LeakyReLU(name="act3", alpha=.01))
    model.add(MaxPooling1D(name="mp3", pool_size=2))

    model.add(Conv1D(name="conv4", filters=2**(filt+3), kernel_size=3))
    model.add(LeakyReLU(name="act4", alpha=.01))
    model.add(MaxPooling1D(name="mp4", pool_size=2))
    
    model.add(Conv1D(name="conv5", filters=2**(filt+4), kernel_size=3))
    model.add(LeakyReLU(name="act5", alpha=.01))
    model.add(MaxPooling1D(name="mp5", pool_size=2))
    
    model.add(Flatten(name="flat1"))
    
    model.add(Dense(name="full1", units=1024))
    model.add(LeakyReLU(name="dact1", alpha=.01))
    model.add(Dropout(name="fdrop1", rate=0.25))

    model.add(Dense(name="full2", units=256))
    model.add(LeakyReLU(name="dact2", alpha=.01))
    model.add(Dropout(name="fdrop2", rate=0.25))
    
    model.add(Dense(name="full3", units=512))
    model.add(LeakyReLU(name="dact3", alpha=.01))
    model.add(Dropout(name="fdrop3", rate=0.25))
    
    model.add(Dense(name="full4", units=512))
    model.add(LeakyReLU(name="dact4", alpha=.01))
    model.add(Dropout(name="fdrop4", rate=0.25))
    
    model.add(Dense(name="full5", units=256))
    model.add(LeakyReLU(name="dact5", alpha=.01))
    model.add(Dropout(name="fdrop5", rate=0.25))

    model.add(Dense(name="last", units=3, activation='softmax'))

    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=[mae, categorical_accuracy])
    return model


========= CrossValidation =========


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Epoch 1/3


  100/43200 [..............................] - ETA: 36:18 - loss: 1.1224 - mean_absolute_error: 0.4486 - categorical_accuracy: 0.2000

  200/43200 [..............................] - ETA: 18:32 - loss: 1.0078 - mean_absolute_error: 0.4176 - categorical_accuracy: 0.3750

...

21100/21600 [============================>.] - ETA: 0s

21400/21600 [============================>.] - ETA: 0s

21600/21600 [==============================] - 7s 346us/step


Results: 0.6720 (0.1735) MSE


[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:  8.0min finished


In [196]:
X_train = np.c_[X_train_eeg1, X_train_eeg2, X_train_emg]


========= CrossValidation =========


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Epoch 1/3


  100/43200 [..............................] - ETA: 36:18 - loss: 1.1224 - mean_absolute_error: 0.4486 - categorical_accuracy: 0.2000

  200/43200 [..............................] - ETA: 18:32 - loss: 1.0078 - mean_absolute_error: 0.4176 - categorical_accuracy: 0.3750

...

21100/21600 [============================>.] - ETA: 0s

21400/21600 [============================>.] - ETA: 0s

21600/21600 [==============================] - 7s 346us/step


Results: 0.6720 (0.1735) MSE


[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:  8.0min finished


In [197]:
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA

ss = StandardScaler()
X_train = ss.fit_transform(X_train)

size = 200

pca = PCA(n_components=size)
X_train = pca.fit_transform(X_train)

X_train = X_train.reshape(-1, size, 1)
"""
X = X_train[0:21600].reshape(-1, 21600, size, 1)
X = np.append(X, X_train[21600:43200].reshape(-1, 21600, size, 1), axis=0)
X = np.append(X, X_train[43200:64800].reshape(-1, 21600, size, 1), axis=0)
X_train = X
"""


========= CrossValidation =========


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Epoch 1/3


  100/43200 [..............................] - ETA: 36:18 - loss: 1.1224 - mean_absolute_error: 0.4486 - categorical_accuracy: 0.2000

  200/43200 [..............................] - ETA: 18:32 - loss: 1.0078 - mean_absolute_error: 0.4176 - categorical_accuracy: 0.3750

...

21100/21600 [============================>.] - ETA: 0s

21400/21600 [============================>.] - ETA: 0s

21600/21600 [==============================] - 7s 346us/step


Results: 0.6720 (0.1735) MSE


[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:  8.0min finished


In [199]:
clf = KerasClassifier(build_fn=cnn_model, epochs=3, batch_size=100, verbose=1)

print("========= CrossValidation =========")
results = cross_val_score(estimator=clf, X=X_train, y=y_train, cv=3, n_jobs=1, scoring=hf.scorer(), 
                          pre_dispatch='n_jobs', verbose=1)
print("Results: %.4f (%.4f) MSE" % (results.mean(), results.std()))


========= CrossValidation =========


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Epoch 1/3


  100/43200 [..............................] - ETA: 36:18 - loss: 1.1224 - mean_absolute_error: 0.4486 - categorical_accuracy: 0.2000

  200/43200 [..............................] - ETA: 18:32 - loss: 1.0078 - mean_absolute_error: 0.4176 - categorical_accuracy: 0.3750

...

21100/21600 [============================>.] - ETA: 0s

21400/21600 [============================>.] - ETA: 0s

21600/21600 [==============================] - 7s 346us/step


Results: 0.6720 (0.1735) MSE


[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:  8.0min finished
